### ✏️ 미니 실습 PJT 과제
#### 알고리즘 A/B 테스트 데이터 분석 -> 발표자 3명 선정
 - 알고리즘 A/B 테스트 데이터셋 : datasets/abtest/algorithm_ab_test.csv
  
 - 분석 준비
   - 데이터셋 구조 파악 (컬럼 설명)
     * user_id: 사용자 ID
  
     * timestamp: 테스트 실행 시간
     * group: 테스트 그룹 (A/B)
     * version: 알고리즘 버전 (v1/v2)
     * conversion: 전환 여부 (0/1)
     * revenue: 수익 금액
   - pandas로 데이터셋 로드 및 전처리
  
   - A/B 테스트 통계적 분석 수행
  
 - 꼭 담겨야할 분석 내용
  
    * 데이터셋 정보 확인
  
    * 데이터셋 기술통계량 확인
    * 데이터셋 pandas 전처리 (결측치 처리, 데이터 타입 변환, 데이터 정렬 등)
    * A/B 테스트 가설 설정
    * 전환율(conversion rate) 분석
    * 수익(revenue) 분석
    * 통계적 유의성 검정 (카이제곱 검정, t-test 등)
    * 시각화 (plotly 사용)
      - 그룹별 전환율 비교
  
      - 그룹별 수익 비교
      - 시간에 따른 전환율/수익 추이
    * 분석 결과 해석 및 결론 도출

## 📑 데이터 전처리

In [23]:
# 데이터 로드
import pandas as pd

df = pd.read_csv('../datasets/abtest/algorithm_ab_test.csv')
df.head()

uid                          ts grp algorithm  converted  amount
0  851227  2025-01-21 22:11:48.556739   A        v1          0       0
1  804351  2025-01-12 08:01:45.159739   A        v1          0       0
2  661713  2025-01-11 16:55:06.154213   B        v2          0   11762
3  853664  2025-01-08 18:28:03.143765   B        v2          0   14987
4  865098  2025-01-21 01:52:26.210827   A        v1          1   13058

In [24]:
# 데이터셋 정보 확인
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 441445 entries, 0 to 441444
Data columns (total 6 columns):
 #   Column     Non-Null Count   Dtype 
---  ------     --------------   ----- 
 0   uid        441445 non-null  int64 
 1   ts         441445 non-null  object
 2   grp        441445 non-null  object
 3   algorithm  441445 non-null  object
 4   converted  441445 non-null  int64 
 5   amount     441445 non-null  int64 
dtypes: int64(3), object(3)
memory usage: 20.2+ MB


In [25]:
# 기술 통계량 확인
df.describe()

uid      converted         amount
count  441445.000000  441445.000000  441445.000000
mean   647245.301326       0.119754    8998.378613
std    230428.065706       0.324675    5877.227027
min    100002.000000       0.000000       0.000000
25%    498388.000000       0.000000       0.000000
50%    709298.000000       0.000000   12103.000000
75%    827644.000000       0.000000   13162.000000
max    946122.000000       1.000000   17778.000000

In [26]:
# 결측치 확인
df.isnull().sum()

uid          0
ts           0
grp          0
algorithm    0
converted    0
amount       0
dtype: int64

In [27]:
# timestamp를 datetime으로 변환
df['ts'] = pd.to_datetime(df['ts'])

In [28]:
# 컬럼명 수정
df = df.rename(columns={
    'uid': 'user_id',
    'ts': 'timestamp', 
    'grp': 'group',
    'algorithm': 'version',
    'converted': 'conversion',
    'amount': 'revenue'
})

In [29]:
# 데이터 정렬
df = df.sort_values('timestamp')

In [30]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 441445 entries, 325747 to 423223
Data columns (total 6 columns):
 #   Column      Non-Null Count   Dtype         
---  ------      --------------   -----         
 0   user_id     441445 non-null  int64         
 1   timestamp   441445 non-null  datetime64[ns]
 2   group       441445 non-null  object        
 3   version     441445 non-null  object        
 4   conversion  441445 non-null  int64         
 5   revenue     441445 non-null  int64         
dtypes: datetime64[ns](1), int64(3), object(2)
memory usage: 23.6+ MB


In [31]:
from scipy.stats import chi2_contingency
from scipy.stats import ttest_ind
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

## 🎯 A/B 테스트 분석
### 1. A/B 테스트 가설 설정
> - 귀무가설(H0): A/B 그룹 간에 전환율 또는 수익에 통계적으로 유의미한 차이가 없다.
> - 대립가설(H1): A/B 그룹 간에 전환율 또는 수익에 통계적으로 유의미한 차이가 있다.

- **유의수준**: α = 0.05

### 가설 설정 검증
✅ **적절성**: 가설이 명확하고 검증 가능하게 설정됨
<br>
✅ **측정 가능성**: 전환율과 수익이라는 명확한 지표 사용
<br>
✅ **실무 연관성**: 비즈니스 목표와 직접 연결된 핵심 지표

### 2. 전환율, 수익 분석 및 유의성 검정

In [32]:
# 3. 전환율(conversion rate) 분석
conversion_by_group = df.groupby('group')['conversion'].agg(['count', 'sum', 'mean'])
conversion_by_group['conversion_rate'] = conversion_by_group['sum'] / conversion_by_group['count'] * 100

print("\n그룹별 전환율:")
print(conversion_by_group)


그룹별 전환율:
        count    sum      mean  conversion_rate
group                                          
A      147202  17723  0.120399        12.039918
B      147276  17514  0.118920        11.891958
C      146967  17628  0.119945        11.994529


In [33]:
# 4. 수익(revenue) 분석
revenue_by_group = df.groupby('group')['revenue'].agg(['count', 'sum', 'mean', 'std'])
print("\n그룹별 수익 분석:")
print(revenue_by_group)


그룹별 수익 분석:
        count         sum          mean          std
group                                               
A      147202   222205001   1509.524334  4097.929864
B      147276  1876946895  12744.417930  1152.393320
C      146967  1873137351  12745.292147  1152.463584


✅ 유의성 검정 통계 방법

- 전환율(이진 데이터): 카이제곱 검정
- 수익(연속형 데이터): 독립표본 t-검정

In [34]:
# 5. 통계적 유의성 검정

# 전환율 차이 검정 (카이제곱 검정)
conversion_contingency = pd.crosstab(df['group'], df['conversion'])
chi2_stat, p_value_conv, dof, expected = chi2_contingency(conversion_contingency)

print("\n전환율 카이제곱 검정 결과:")
print(f"p-value: {p_value_conv:.4f}")

# 수익 차이 검정 (독립표본 t-검정)
group_a_revenue = df[df['group'] == 'A']['revenue']
group_b_revenue = df[df['group'] == 'B']['revenue']
t_stat, p_value_rev = ttest_ind(group_a_revenue, group_b_revenue)

print("\n수익 t-검정 결과:")
print(f"p-value: {p_value_rev:.4f}")


전환율 카이제곱 검정 결과:
p-value: 0.4482

수익 t-검정 결과:
p-value: 0.0000


🔍 전환율 분석:
   - 카이제곱 검정 p-value: 0.4482
   - 유의수준: 0.05
   - 결과: 통계적으로 유의한 차이 없음
   - 해석: p-value (0.4482) > α (0.05) → 귀무가설 기각 실패
   - B그룹의 전환율 개선 효과가 통계적으로 입증되지 않음. 현재 데이터로는 새로운 버전으로 전환할 근거 부족.

💰 수익 분석:
   - t-검정 p-value: 0.0 (< 0.0001)
   - 유의수준: 0.05
   - 결과: 통계적으로 유의한 차이 있음
   - 해석: p-value (< 0.0001) < α (0.05) → 귀무가설 기각
   - B그룹에서 수익 개선 효과가 통계적으로 유의미함. 새로운 버전이 수익성 관점에서 우수한 성과를 보임.

### 3. 데이터 시각화

In [37]:
# 6. 시각화

# 그룹별 전환율 비교
conversion_rate = df.groupby('group')['conversion'].mean().reset_index()
conversion_rate.columns = ['group', 'conversion_rate']

fig_conv = px.bar(
    conversion_by_group.reset_index(),
    x='group',
    y='conversion_rate',
    title='그룹별 전환율 비교',
    labels={'conversion_rate': '전환율 (%)', 'group': '그룹'}
)
fig_conv.show()

In [40]:
# 그룹별 평균 수익 비교
fig_rev = px.box(
    df,
    x='group',
    y='revenue',
    title='그룹별 수익 분포',
    labels={'revenue': '수익', 'group': '그룹'}
)
fig_rev.show()

In [41]:
from plotly.subplots import make_subplots

In [42]:
# 시간에 따른 지표 추이
df['date'] = df['timestamp'].dt.date
daily_metrics = df.groupby(['date', 'group']).agg({
    'conversion': 'mean',
    'revenue': 'mean'
}).reset_index()

In [ ]:
fig = make_subplots(rows=2, cols=1,
                    subplot_titles=('일별 전환율 추이', '일별 평균 수익 추이'),
                    vertical_spacing=0.15)

# 전환율 추이 그래프 추가
for group in df['group'].unique():
    group_data = daily_metrics[daily_metrics['group'] == group]
    fig.add_trace(
        go.Scatter(x=group_data['date'], 
                  y=group_data['conversion'],
                  name=f'Group {group} - 전환율',
                  mode='lines'),
        row=1, col=1
    )

# 수익 추이 그래프 추가
for group in df['group'].unique():
    group_data = daily_metrics[daily_metrics['group'] == group]
    fig.add_trace(
        go.Scatter(x=group_data['date'], 
                  y=group_data['revenue'],
                  name=f'Group {group} - 수익',
                  mode='lines'),
        row=2, col=1
    )

# 레이아웃 업데이트
fig.update_layout(height=800, 
                 title_text='일별 전환율 및 평균 수익 추이',
                 showlegend=True)

fig.update_xaxes(title_text='날짜', row=1, col=1)
fig.update_xaxes(title_text='날짜', row=2, col=1)
fig.update_yaxes(title_text='전환율', row=1, col=1)
fig.update_yaxes(title_text='평균 수익', row=2, col=1)

fig.show()

## 4. 결과 해석

### 핵심 발견사항
1. **전환율**: B그룹이 A그룹 대비 유의한 개선을 보이지 않음
2. **수익성**: B그룹이 A그룹 대비 유의한 수익 증가를 보임
3. 전환율은 비슷하지만 수익성은 개선된 상황

### 추천 의사결정
**🟢 B그룹 도입 권장**
- 수익 최적화가 주요 목표인 경우 통계적으로 유의한 수익 증가 확인

### ⚠️ 추가 고려사항
- 통계적 유의성 외에 실제 효과 크기 검토 필요
- 표본 크기가 차이를 감지하기에 충분한지 확인
- 세그먼트 분석을 통한 사용자 특성별 효과 차이 분석
- 시계열 분석을 통한 계절성 및 트렌드 효과 분석